Azure GET CLI Details

In [4]:
import os
import pandas as pd
from azure.identity import DefaultAzureCredential
from azure.mgmt.compute import ComputeManagementClient
from dotenv import load_dotenv
load_dotenv()

True

In [5]:
subscription_id = os.getenv('AZURE_SUBSCRIPTION_ID')
print("Subscription ID:", subscription_id)
credential = DefaultAzureCredential()
print("Using DefaultAzureCredential -> will authenticate via env vars or CLI login")
compute_client = ComputeManagementClient(credential, subscription_id)
print(compute_client)
print("Compute client ready for region-by-region VM SKU queries")

Subscription ID: 90907ac8-01bc-4bff-9a9b-8eaa2e390062
Using DefaultAzureCredential -> will authenticate via env vars or CLI login
Compute client ready for region-by-region VM SKU queries


In [6]:
def collect_all_vm_sizes(compute_client: ComputeManagementClient):

    rows = []
    for sku in compute_client.resource_skus.list():
        # Only virtual machine SKUs
        if sku.resource_type.lower() != 'virtualmachines':
            continue

        # Map capabilities list to a dict for lookup
        caps = {c.name: c.value for c in sku.capabilities}

        # Expand each location the SKU is offered in
        for loc_info in sku.location_info:
            loc = loc_info.location
            rows.append({
                'Region':              loc,
                'VMSize':              sku.name,
                'vCPUs':               int(caps.get('vCPUs', 0)),
                'Memory (GiB)':        float(caps.get('MemoryGB', 0)),
                'OS Disk Size (GB)':   float(caps.get('OSVhdSizeMB', 0)) / 1024,
                'Temp Disk Size (GB)': float(caps.get('ResourceDiskSizeMB', 0)) / 1024,
                'Max Data Disks':      int(caps.get('MaxDataDiskCount', 0)),
                'Network BW (Gbps)':   float(caps.get('NetworkBandwidthInGbps', 0)),
                'GPU Count':           int(caps.get('GPUs', 0)),
            })

    return pd.DataFrame(rows)

In [7]:
df_vm_sizes = collect_all_vm_sizes(compute_client)

# 4. Inspect
print(df_vm_sizes.head())
print("Total SKUs:", len(df_vm_sizes))

               Region    VMSize  vCPUs  Memory (GiB)  OS Disk Size (GB)  \
0       australiaeast  Basic_A0      1          0.75             1023.0   
1  australiasoutheast  Basic_A0      1          0.75             1023.0   
2         brazilsouth  Basic_A0      1          0.75             1023.0   
3       CanadaCentral  Basic_A0      1          0.75             1023.0   
4          CanadaEast  Basic_A0      1          0.75             1023.0   

   Temp Disk Size (GB)  Max Data Disks  Network BW (Gbps)  GPU Count  
0                  0.0               1                0.0          0  
1                  0.0               1                0.0          0  
2                  0.0               1                0.0          0  
3                  0.0               1                0.0          0  
4                  0.0               1                0.0          0  
Total SKUs: 42645


In [9]:
print(df_vm_sizes.to_string())

                   Region                      VMSize  vCPUs  Memory (GiB)  OS Disk Size (GB)  Temp Disk Size (GB)  Max Data Disks  Network BW (Gbps)  GPU Count
0           australiaeast                    Basic_A0      1          0.75             1023.0                  0.0               1                0.0          0
1      australiasoutheast                    Basic_A0      1          0.75             1023.0                  0.0               1                0.0          0
2             brazilsouth                    Basic_A0      1          0.75             1023.0                  0.0               1                0.0          0
3           CanadaCentral                    Basic_A0      1          0.75             1023.0                  0.0               1                0.0          0
4              CanadaEast                    Basic_A0      1          0.75             1023.0                  0.0               1                0.0          0
5            CentralIndia         

In [10]:
print("Number of rows:", df_vm_sizes.shape[0])  # Total rows
print("Number of columns:", df_vm_sizes.shape[1])  # Total columns
print(df_vm_sizes.count())

Number of rows: 42645
Number of columns: 9
Region                 42645
VMSize                 42645
vCPUs                  42645
Memory (GiB)           42645
OS Disk Size (GB)      42645
Temp Disk Size (GB)    42645
Max Data Disks         42645
Network BW (Gbps)      42645
GPU Count              42645
dtype: int64


In [11]:
output_path = "azure_vm_sizes_data.csv"
df_vm_sizes.to_csv(output_path, index=False)

print(f"Exported {len(df_vm_sizes)} rows to {output_path}")

Exported 42645 rows to azure_vm_sizes_data.csv
